In [249]:
!pip install simpletransformers

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [250]:
import pandas as pd
import sklearn

In [251]:
import torch
torch.cuda.is_available()

True

In [252]:
def load_dataset(file_name):
    import pandas as pd
    import json
    
    df = []
    with open(file_name, encoding='utf-8') as f:
        for i in f:
            i = eval(i)

            tweet = i['postText']
            label = i['tags']

            assert len(tweet) == 1
            tweet = tweet[0]
            
            assert len(label) == 1
            label = label[0]
            
            if label not in ['phrase', 'phrases', 'passage', 'multi']:
                print(label)
                
            assert label in ['phrase', 'phrases', 'passage', 'multi']
            
            
            df += [i]

    return pd.DataFrame(df)   
            
    
# test_dataset = load_dataset('test.jsonl')
train_dataset = load_dataset('train.jsonl')
validation_dataset = load_dataset('validation.jsonl')

In [253]:
train_dataset.head(5)

uuid              postId  \
0  0af11f6b-c889-4520-9372-66ba25cb7657              532quh   
1  b1a1f63d-8853-4a11-89e8-6b2952a393ec  411701128456593408   
2  008b7b19-0445-4e16-8f9e-075b73f80ca4  380537005123190784   
3  31ecf93c-3e21-4c80-949b-aa549a046b93  844567852531286016   
4  31b108a3-c828-421a-a4b9-cf651e9ac859  814186311573766144   

                                            postText postPlatform  \
0  [Wes Welker Wanted Dinner With Tom Brady, But ...       reddit   
1   [NASA sets date for full recovery of ozone hole]      Twitter   
2  [This is what makes employees happy -- and it'...      Twitter   
3  [Passion is overrated — 7 work habits you need...      Twitter   
4  [The perfect way to cook rice so that it's per...      Twitter   

                                    targetParagraphs  \
0  [It’ll be just like old times this weekend for...   
1  [2070 is shaping up to be a great year for Mot...   
2  [Despite common belief, money isn't the key to...   
3  [It’s common wisdom. Near gospel really, and n...   
4  [Boiling rice may seem simple, but there is a ...   

                                         targetTitle  \
0  Wes Welker Wanted Dinner With Tom Brady, But P...   
1  Hole In Ozone Layer Expected To Make Full Reco...   
2  Intellectual Stimulation Trumps Money For Empl...   
3  ‘Follow your passion’ is wrong, here are 7 hab...   
4  Revealed: The perfect way to cook rice so that...   

                                   targetDescription  \
0  It'll be just like old times this weekend for ...   
1  2070 is shaping up to be a great year for Moth...   
2  By: Chad Brooks \r\nPublished: 09/18/2013 06:4...   
3    There's a lot more to work that loving your job   
4  The question 'How does one cook rice properly?...   

                                      targetKeywords  \
0    new england patriots, ricky doyle, top stories,   
1  ozone layer,ozone hole determined by weather,M...   
2  employee happiness money,employee happiness in...   
3                       business, work-life, careers   
4            Quora,users,share,perfect,way,cook,rice   

                                         targetMedia  \
0  [http://pixel.wp.com/b.gif?v=noscript, http://...   
1  [http://s.m.huffpost.com/assets/Logo_Huffingto...   
2  [http://i.huffpost.com/gen/1359674/images/o-HA...   
3                                               None   
4                                               None   

                                           targetUrl  \
0  http://nesn.com/2016/09/wes-welker-wanted-dinn...   
1                             http://huff.to/1cH672Z   
2                             http://huff.to/1epfeaw   
3                                               None   
4                                               None   

                                          provenance  \
0  {'source': 'anonymized', 'humanSpoiler': 'They...   
1  {'source': 'anonymized', 'humanSpoiler': '2070...   
2  {'source': 'anonymized', 'humanSpoiler': 'Inte...   
3  {'source': 'anonymized', 'humanSpoiler': None,...   
4  {'source': 'anonymized', 'humanSpoiler': None,...   

                                             spoiler  \
0              [how about that morning we go throw?]   
1                                             [2070]   
2                         [intellectual stimulation]   
3  [Purpose connects us to something bigger and i...   
4                                 [in a rice cooker]   

                                    spoilerPositions       tags  
0                             [[[3, 151], [3, 186]]]  [passage]  
1                                 [[[0, 0], [0, 4]]]   [phrase]  
2                             [[[1, 186], [1, 210]]]   [phrase]  
3  [[[11, 25], [11, 101]], [[17, 56], [17, 85]], ...    [multi]  
4                               [[[5, 60], [5, 76]]]   [phrase]

Dropping Null values from dataset

In [254]:
train_dataset.dropna(inplace=True)

In [255]:
validation_dataset.dropna(inplace=True)

In [256]:
train_dataset.reset_index(inplace=True)

In [257]:
validation_dataset.reset_index(inplace=True)

Processing the data in SQuAD format to pass in Question Answering Model

In [258]:
train = []
for i in range(train_dataset.shape[0]):
    a = train_dataset.loc[i]
    d = {}
    d['context'] = ' '.join(a['targetParagraphs'])
    e = []
    uuid = a['uuid']
    if len(a['spoiler']) == 0:
      continue
    for i in range(len(a['spoilerPositions'])):
        id = uuid +' '+ str(i)
        question = a['postText'][0]
        answers = [{'text':a['spoiler'][i], 'answer_start':d['context'].find(a['spoiler'][i])}]   
        e.append( { 'id':id,'question':question,'answers':answers})
    d['qas'] = e 
    train.append(d)

In [259]:
train[-3]

{'context': 'If you\'re a vegetarian, we have some good news for you: Munching on all those plants may cut your risk for colorectal cancer -- the second leading cause of cancer death in the U.S. -- by about 20 percent. For the study, published in the March 9 online edition of JAMA Internal Medicine, researchers kept track of 77,000 men and women over the course of seven years. Roughly half the participants were meat-eaters, and the others fell into four vegetarian-like groups: Semi-vegetarians (ate meat less than once a week), pesco-vegetarians (ate fish but not other meat), lacto-ovo vegetarians (ate eggs and dairy but no meat) and vegans (no meat, no dairy, no eggs). Researchers found that after seven years, there were 380 colon cancer cases and 110 rectal cancer cases among the group. As it turns out, vegetarians were less likely to develop the disease compared to participants who ate meat, but pesco-vegetarians, in particular, were the real winners. "All vegetarians together had on

In [260]:
test = []
for i in range(validation_dataset.shape[0]):
    a = validation_dataset.loc[i]
    d = {}
    d['context'] = ' '.join(a['targetParagraphs'])
    e = []
    uuid = a['uuid']
    if len(a['spoiler']) == 0:
      continue
    for i in range(len(a['spoiler'])):
        id = uuid +' '+ str(i)
        question = a['postText'][0]
        answers = [{'text':a['spoiler'][i], 'answer_start':d['context'].find(a['spoiler'][i])}] 
        e.append( { 'id':id,'question':question,'answers':answers})
    d['qas'] = e 
    test.append(d)

In [261]:
test[-1]

{'context': 'Richard Belzer is leaving "Law & Order: SVU." Belzer, who has been with the show since it began 15 seasons ago, is leaving "SVU" as a series regular. He\'s been playing the character of John Munch for more than 20 years. Belzer\'s character turned in his retirement papers at the end of the Wed., Oct. 9 episode of "SVU." Look for his retirement party in the Oct. 16 episode. While he may be leaving the show as a series regular, don\'t expect Belzer to say goodbye to the character of John Munch forever. A source confirmed Belzer is expected to make recurring appearances on the long-running NBC drama. "I\'d be a fool to say I didn\'t want to do it anymore and I\'m certainly not bored with the character because the writing is so good," Belzer told The Huffington Post in May 2013. "[Munch is] very close to how I would be if I were in that situation, so it\'s a dream." The character of John Munch first made his debut on "Homicide: Life on the Street" in 1993. The character has al

Importing QuestionAnswering Model

In [262]:
from simpletransformers.question_answering import QuestionAnsweringModel, QuestionAnsweringArgs

In [263]:
model_args = QuestionAnsweringArgs()
model_args.train_batch_size = 32

RoBERTa model for question answering

In [264]:
model = QuestionAnsweringModel(
    "roberta", "roberta-base",
    args=model_args,
    use_cuda = True
)

Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForQuestionAnswering: ['lm_head.decoder.weight', 'lm_head.bias', 'lm_head.dense.weight', 'lm_head.layer_norm.bias', 'lm_head.layer_norm.weight', 'lm_head.dense.bias']
- This IS expected if you are initializing RobertaForQuestionAnswering from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForQuestionAnswering from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForQuestionAnswering were not initialized from the model checkpoint at roberta-base and are newly initialized: ['qa_outputs.bias', 'qa_outputs.weight']
You should probably TRAIN this model on a down-stream task to be able to use 

In [265]:
model.train_model(train)

convert squad examples to features:   0%|          | 0/1843 [00:00<?, ?it/s]Could not find answer: '' vs. ''Pirates 5' Release Date Shifted To 2016'
Could not find answer: '' vs. 'Pays For 16 Struggling Families' Back-To-School Supplies At Kmar'
Could not find answer: '' vs. 'Monuments Under Construction'
Could not find answer: '' vs. 'Don't click'
Could not find answer: '' vs. 'BFFs Kanye West and Paul McCartney hang out at Stella show in Paris'
Could not find answer: '' vs. ''To Kill a Mockingbird''
Could not find answer: '' vs. 'White Supremacists'
Could not find answer: '' vs. 'VR Porn Therapy'
Could not find answer: '' vs. 'Sexy Bondage Dress'
Could not find answer: '' vs. 'Star Wars: Episode VIII's director jokes it won't come to cinemas'
Could not find answer: '' vs. 'lack of banter'
Could not find answer: '' vs. 'One In Ten'
Could not find answer: '' vs. 'In-Flight Internet'
Could not find answer: '' vs. '11 Centimeters'
Could not find answer: '' vs. 'Colorado Sheriffs'
Could n

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/122 [00:00<?, ?it/s]

/usr/local/lib/python3.9/dist-packages/torch/optim/lr_scheduler.py:139: UserWarning: Detected call of `lr_scheduler.step()` before `optimizer.step()`. In PyTorch 1.1.0 and later, you should call them in the opposite order: `optimizer.step()` before `lr_scheduler.step()`.  Failure to do this will result in PyTorch skipping the first value of the learning rate schedule. See more details at https://pytorch.org/docs/stable/optim.html#how-to-adjust-learning-rate
  warnings.warn("Detected call of `lr_scheduler.step()` before `optimizer.step()`. "


(122, 1.885745674860282)

Viewing the results

In [266]:
# Evaluate the model
result, texts = model.eval_model(test)

add example index and unique id: 100%|██████████| 454/454 [00:00<00:00, 209070.49it/s]


Running Evaluation:   0%|          | 0/141 [00:00<?, ?it/s]

In [267]:
result

{'correct': 1, 'similar': 451, 'incorrect': 2, 'eval_loss': -3.168786015070922}

In [268]:
answers, prob = model.predict(test)

add example index and unique id: 100%|██████████| 454/454 [00:00<00:00, 350361.36it/s]


Running Prediction:   0%|          | 0/141 [00:00<?, ?it/s]

In [269]:
answers

[{'id': '8b713277-0e5b-4873-a216-b650f21f3b4c 0',
  'answer': ['',
   'CBGB.',
   "punk music's evolution can be traced back, more or less, to one singular staple: CBGB.",
   "CBGB. Opened in 1973 in downtown Manhattan's East Village,",
   "CBGB. Opened in 1973 in downtown Manhattan's East Village, the nightclub that originally intended to house country, bluegrass and blues music (hint its acronym) quickly became a breeding ground for bands like The Ramones, Talking Heads and The Police, among countless others.",
   "CBGB. Opened in 1973 in downtown Manhattan's East Village, the nightclub that originally intended to house country, bluegrass and blues music (hint its acronym) quickly became a breeding ground for bands like The Ramones, Talking Heads and The Police, among countless others. The legacy of the club, which closed in 2006 over a rent dispute,",
   'CBGB. Opened in 1973',
   "CBGB. Opened in 1973 in downtown Manhattan's East Village, the nightclub",
   "punk music's evolution 

In [270]:
!rm -rf outputs

Using BERT

In [271]:
model = QuestionAnsweringModel(
    "bert", "bert-base-cased",
    args=model_args,
    use_cuda = True
)

Some weights of the model checkpoint at bert-base-cased were not used when initializing BertForQuestionAnswering: ['cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.bias', 'cls.predictions.bias', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.decoder.weight', 'cls.predictions.transform.dense.weight']
- This IS expected if you are initializing BertForQuestionAnswering from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForQuestionAnswering from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForQuestionAnswering were not initialized from the model checkpoint at bert-base-cased and a

In [272]:
model.train_model(train)

convert squad examples to features:   0%|          | 0/1843 [00:00<?, ?it/s]Could not find answer: '' vs. ''Pirates 5' Release Date Shifted To 2016'
Could not find answer: '' vs. 'Pays For 16 Struggling Families' Back-To-School Supplies At Kmar'
Could not find answer: '' vs. 'Monuments Under Construction'
Could not find answer: '' vs. 'Don't click'
Could not find answer: '' vs. 'BFFs Kanye West and Paul McCartney hang out at Stella show in Paris'
Could not find answer: '' vs. ''To Kill a Mockingbird''
Could not find answer: '' vs. 'White Supremacists'
Could not find answer: '' vs. 'VR Porn Therapy'
Could not find answer: '' vs. 'Sexy Bondage Dress'
Could not find answer: '' vs. 'Star Wars: Episode VIII's director jokes it won't come to cinemas'
Could not find answer: '' vs. 'lack of banter'
Could not find answer: '' vs. 'One In Ten'
Could not find answer: '' vs. 'In-Flight Internet'
Could not find answer: '' vs. '11 Centimeters'
Could not find answer: '' vs. 'Colorado Sheriffs'
Could n

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/127 [00:00<?, ?it/s]

(127, 1.6125224978905024)

In [273]:
# Evaluate the model
result, texts = model.eval_model(test)

add example index and unique id: 100%|██████████| 454/454 [00:00<00:00, 266621.96it/s]


Running Evaluation:   0%|          | 0/145 [00:00<?, ?it/s]

In [274]:
result

{'correct': 434, 'similar': 20, 'incorrect': 0, 'eval_loss': -3.73046875}

In [275]:
answers, prob = model.predict(test)

add example index and unique id: 100%|██████████| 454/454 [00:00<00:00, 263632.01it/s]


Running Prediction:   0%|          | 0/145 [00:00<?, ?it/s]

In [276]:
answers

[{'id': '8b713277-0e5b-4873-a216-b650f21f3b4c 0',
  'answer': ['',
   'CBGB',
   "CBGB. Opened in 1973 in downtown Manhattan's East Village, the nightclub that originally intended to house country, bluegrass and blues music (hint its acronym) quickly became a breeding ground for bands like The Ramones, Talking Heads and The Police",
   "CBGB. Opened in 1973 in downtown Manhattan's East Village",
   'Colonel Brandon',
   "CBGB. Opened in 1973 in downtown Manhattan's East Village, the nightclub that originally intended to house country, bluegrass and blues music",
   'CBGB.',
   "CBGB. Opened in 1973 in downtown Manhattan's East Village, the nightclub that originally intended to house country, bluegrass and blues music (hint its acronym) quickly became a breeding ground for bands like The Ramones",
   "Justin [Bartha] as well. ... There’s quite a lot of ass in the film. You had to try out an American accent in this role. Is there an accent out there that you'd be intimidated to have to u

In [277]:
!rm -rf outputs/

Using ALBERT

In [278]:
model = QuestionAnsweringModel(
    "albert", "albert-base-v2",
    args=model_args,
    use_cuda = True
)

Some weights of the model checkpoint at albert-base-v2 were not used when initializing AlbertForQuestionAnswering: ['predictions.decoder.bias', 'predictions.dense.bias', 'predictions.LayerNorm.bias', 'predictions.LayerNorm.weight', 'predictions.dense.weight', 'predictions.decoder.weight', 'predictions.bias']
- This IS expected if you are initializing AlbertForQuestionAnswering from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing AlbertForQuestionAnswering from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of AlbertForQuestionAnswering were not initialized from the model checkpoint at albert-base-v2 and are newly initialized: ['qa_outputs.weight', 'qa_outputs.bias']
You should probably TRAIN t

In [279]:
model.train_model(train)

convert squad examples to features:   0%|          | 0/1843 [00:00<?, ?it/s]Could not find answer: '' vs. ''Pirates 5' Release Date Shifted To 2016'
Could not find answer: '' vs. 'Pays For 16 Struggling Families' Back-To-School Supplies At Kmar'
Could not find answer: '' vs. 'Monuments Under Construction'
Could not find answer: '' vs. 'Don't click'
Could not find answer: '' vs. 'BFFs Kanye West and Paul McCartney hang out at Stella show in Paris'
Could not find answer: '' vs. ''To Kill a Mockingbird''
Could not find answer: '' vs. 'White Supremacists'
Could not find answer: '' vs. 'VR Porn Therapy'
Could not find answer: '' vs. 'Sexy Bondage Dress'
Could not find answer: '' vs. 'Star Wars: Episode VIII's director jokes it won't come to cinemas'
Could not find answer: '' vs. 'lack of banter'
Could not find answer: '' vs. 'One In Ten'
Could not find answer: '' vs. 'In-Flight Internet'
Could not find answer: '' vs. '11 Centimeters'
Could not find answer: '' vs. 'Colorado Sheriffs'
Could n

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/155 [00:00<?, ?it/s]

(155, 1.0186590265843176)

In [280]:
# Evaluate the model
result, texts = model.eval_model(test)

add example index and unique id: 100%|██████████| 454/454 [00:00<00:00, 171875.98it/s]


Running Evaluation:   0%|          | 0/173 [00:00<?, ?it/s]

In [281]:
result

{'correct': 399,
 'similar': 55,
 'incorrect': 0,
 'eval_loss': -1.2243384212427746}

In [282]:
answers, prob = model.predict(test)

add example index and unique id: 100%|██████████| 454/454 [00:00<00:00, 142190.41it/s]


Running Prediction:   0%|          | 0/173 [00:00<?, ?it/s]

In [283]:
answers

[{'id': '8b713277-0e5b-4873-a216-b650f21f3b4c 0',
  'answer': ['',
   "CBGB. Opened in 1973 in downtown Manhattan's East Village,",
   'East Village,',
   'CBGB.',
   "CBGB. Opened in 1973 in downtown Manhattan's",
   "The mythology of punk music's evolution can be traced back, more or less, to one singular staple: CBGB. Opened in 1973 in downtown Manhattan's East Village,",
   "punk music's evolution can be traced back, more or less, to one singular staple: CBGB. Opened in 1973 in downtown Manhattan's East Village,",
   'Play-Doh can that I made. You know Play-Doh? Of course. Grint: Well, literally, I actually made it. It was a yellow bin.',
   'Of course. Grint: Well, literally, I actually made it. It was a yellow bin.',
   'a Play-Doh can that I made. You know Play-Doh? Of course. Grint: Well, literally, I actually made it. It was a yellow bin.',
   'There was quite a lot of that in the film. Especially from Justin [Bartha] as well. ... There’s quite a lot of ass in the film. You ha